In [128]:
from __future__ import print_function

from keras.models import Sequential, Model
from keras.layers.embeddings import Embedding
from keras.layers import Input, Activation, Dense, Permute, Dropout, add, dot,merge, concatenate
from keras.layers import LSTM
from keras.utils.data_utils import get_file
from keras.preprocessing.sequence import pad_sequences
from functools import reduce
import tarfile
import numpy as np
import re

In [129]:
def tokenize(sent):
    # splitting the sentences based on spaces and tokenizing them
    return [x.strip() for x in re.split('(\W+)?', sent) if x.strip()]



In [130]:
def parse_stories(lines, only_supporting=False):
   
    # Trying to retrive the questions and 
    # ansers to the particular questions
    
    data = []
    story = []
    for line in lines:
        line = line.decode('utf-8').strip()
        nid, line = line.split(' ', 1)
        nid = int(nid)
        if nid == 1:
            story = []
        if '\t' in line:
            q, a, supporting = line.split('\t')
            q = tokenize(q)
            substory = None
            if only_supporting:
                # Only select the related substory
                supporting = map(int, supporting.split())
                substory = [story[i - 1] for i in supporting]
            else:
                # Provide all the substories
                substory = [x for x in story if x]
            data.append((substory, q, a))
            story.append('')
        else:
            sent = tokenize(line)
            story.append(sent)
        
    return data


In [131]:
def get_stories(f, only_supporting=False, max_length=None):
    
    # Discaring the stories longer than the max length defined 
    # and converting the lines in to a single story corresponding 
    # to the questions
    data = parse_stories(f.readlines(), only_supporting=only_supporting)
    flatten = lambda data: reduce(lambda x, y: x + y, data)
    data = [(flatten(story), q, answer) for story, q, answer in data if not max_length or len(flatten(story)) < max_length]
    return data


In [132]:
def vectorize_stories(data, word_idx, story_maxlen, query_maxlen):

    # Mapping the length of stories against story with maximum
    # length and doing necessary padding
    
    X = []
    Xq = []
    Y = []
    for story, query, answer in data:
        x=[word_idx[w] for w in story]
        xq=[word_idx[w] for w in query]
        y=np.zeros(len(word_idx) + 1)
        y[word_idx[answer]]=1
        X.append(x)
        Xq.append(xq)
        Y.append(y)
    return (pad_sequences(X, maxlen=story_maxlen),
            pad_sequences(Xq, maxlen=query_maxlen),
            np.array(Y))


In [133]:
''' Accessing the particula modules of the 
Babi dataset saperated by the modules
'''

try:
    path = get_file('babi-tasks-v1-2.tar.gz', origin='https://s3.amazonaws.com/text-datasets/babi_tasks_1-20_v1-2.tar.gz')
except:
    print('Error downloading dataset, please download it manually:\n'
          '$ wget http://www.thespermwhale.com/jaseweston/babi/tasks_1-20_v1-2.tar.gz\n'
          '$ mv tasks_1-20_v1-2.tar.gz ~/.keras/datasets/babi-tasks-v1-2.tar.gz')
    raise
tar = tarfile.open(path)


In [134]:
challenges = {'qa11_basic-coreference': 'tasks_1-20_v1-2/en-10k/qa11_basic-coreference_{}.txt'}
challenge_type = 'qa11_basic-coreference'
challenge = challenges[challenge_type]

print('Extracting stories for the challenge:', challenge_type)
train_stories = get_stories(tar.extractfile(challenge.format('train')))
test_stories = get_stories(tar.extractfile(challenge.format('test')))

Extracting stories for the challenge: qa11_basic-coreference


/usr/lib/python3.5/re.py:203: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


In [135]:
print(train_stories)

[(['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.'], ['Where', 'is', 'Mary', '?'], 'bedroom'), (['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'Daniel', '?'], 'hallway'), (['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'hallway', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'Daniel', '?'], 'hallway'), (['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'move

In [136]:
print(test_stories)

[(['John', 'journeyed', 'to', 'the', 'hallway', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.'], ['Where', 'is', 'John', '?'], 'garden'), (['John', 'journeyed', 'to', 'the', 'hallway', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Following', 'that', 'he', 'went', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'John', '?'], 'hallway'), (['John', 'journeyed', 'to', 'the', 'hallway', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Following', 'that', 'he', 'went', 'to', 'the', 'hallway', '.', 'Sandra', 'travelled', 'to', 'the', 'bedroom', '.', 'Then', 'she', 'moved', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'Sandra', '?'], 'hallway'), (['John', 'journeyed', 'to', 'the', 'hallway', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Following', 'that', 'he', 'went', 't

In [137]:
vocab = set()
for story, q, answer in train_stories + test_stories:
    print(story)
    vocab |= set(story + q + [answer])
vocab = sorted(vocab)

# Reserve 0 for masking via pad_sequences
vocab_size = len(vocab) + 1
story_maxlen = max(map(len, (x for x, _, _ in train_stories + test_stories)))
query_maxlen = max(map(len, (x for _, x, _ in train_stories + test_stories)))

['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.']
['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'hallway', '.']
['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'hallway', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'hallway', '.']
['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'hallway', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'hall

['John', 'journeyed', 'to', 'the', 'bathroom', '.', 'Afterwards', 'he', 'went', 'to', 'the', 'kitchen', '.', 'John', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Following', 'that', 'he', 'moved', 'to', 'the', 'kitchen', '.']
['John', 'journeyed', 'to', 'the', 'bathroom', '.', 'Afterwards', 'he', 'went', 'to', 'the', 'kitchen', '.', 'John', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Following', 'that', 'he', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'bathroom', '.']
['John', 'journeyed', 'to', 'the', 'bathroom', '.', 'Afterwards', 'he', 'went', 'to', 'the', 'kitchen', '.', 'John', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Following', 'that', 'he', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Following', 'that', 

['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'moved', 'to', 'the', 'garden', '.']
['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'moved', 'to', 'the', 'garden', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Afterwards', 'she', 'travelled', 'to', 'the', 'office', '.']
['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'moved', 'to', 'the', 'garden', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Afterwards', 'she', 'travelled', 'to', 'the', 'office', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Then', 'she', 'travelled', 'to', 'the', 'kitchen', '.']
['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'moved', 'to', 'the', 'garden', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Afterwards', 'she', 'travelled', 'to', 'the', 'office', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Then', 'she', 'travelled', 'to', 'the', 'kitchen', '.', 'San

['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'garden', '.']
['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'office', '.']
['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Following', 'that', 'she', 'travelled', 'to', 'the', 'bathroom', '.']
['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'After', 'that', 'she', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'travelled', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedro

['Sandra', 'moved', 'to', 'the', 'office', '.', 'Then', 'she', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'to', 'the', 'bedroom', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'journeyed', 'to', 'the', 'hallway', '.']
['Sandra', 'moved', 'to', 'the', 'office', '.', 'Then', 'she', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'to', 'the', 'bedroom', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'kitchen', '.', 'After', 'that', 'she', 'travelled', 'to', 'the', 'garden', '.']
['Sandra', 'moved', 'to', 'the', 'office', '.', 'Then', 'she', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'to', 'the', 'bedroom', '.', 'Afterwards', 'he', 'moved', 'to', 'the', 'kitchen', '.', 'San

['Daniel', 'moved', 'to', 'the', 'office', '.', 'Then', 'he', 'went', 'to', 'the', 'garden', '.']
['Daniel', 'moved', 'to', 'the', 'office', '.', 'Then', 'he', 'went', 'to', 'the', 'garden', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Then', 'she', 'went', 'to', 'the', 'office', '.']
['Daniel', 'moved', 'to', 'the', 'office', '.', 'Then', 'he', 'went', 'to', 'the', 'garden', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Then', 'she', 'went', 'to', 'the', 'office', '.', 'Sandra', 'travelled', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'went', 'back', 'to', 'the', 'bedroom', '.']
['Daniel', 'moved', 'to', 'the', 'office', '.', 'Then', 'he', 'went', 'to', 'the', 'garden', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Then', 'she', 'went', 'to', 'the', 'office', '.', 'Sandra', 'travelled', 'to', 'the', 'hallway', '.', 'Following', 'that', 'she', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'to', 'the', 'bedroom', '.', 'After', 'that', 'she', '

In [138]:
with open('story_maxlen_basic-coreference.txt','w') as file:
    file.write(str(story_maxlen))
    file.write('\n')
file.close()


with open('query_maxlen_basic-coreference.txt','w') as file:
    file.write(str(query_maxlen))
    file.write('\n')
file.close()


In [139]:
''' Knowing some facts and stats about the 
module of dataset we are using
'''

print('-')
print('Vocab size:', vocab_size, 'unique words')
print('Story max length:', story_maxlen, 'words')
print('Query max length:', query_maxlen, 'words')
print('Number of training stories:', len(train_stories))
print('Number of test stories:', len(test_stories))
print('-')
print('Here\'s what a "story" tuple looks like (input, query, answer):')
print(train_stories[0])
print('-')
print('Vectorizing the word sequences...')

word_idx = dict((c, i + 1) for i, c in enumerate(vocab))
idx_word = dict((i+1, c) for i,c in enumerate(vocab))
inputs_train, queries_train, answers_train = vectorize_stories(train_stories,
                                                               word_idx,
                                                               story_maxlen,
                                                               query_maxlen)
inputs_test, queries_test, answers_test = vectorize_stories(test_stories,
                                                            word_idx,
                                                            story_maxlen,
                                                            query_maxlen)

-
Vocab size: 29 unique words
Story max length: 76 words
Query max length: 4 words
Number of training stories: 10000
Number of test stories: 1000
-
Here's what a "story" tuple looks like (input, query, answer):
(['Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bedroom', '.'], ['Where', 'is', 'Mary', '?'], 'bedroom')
-
Vectorizing the word sequences...


In [140]:
with open('word_idx_basic-coreference.txt','w') as file:
    file.write(str(word_idx))
file.close()

In [141]:
with open('idx_word_basic-coreference.txt','w') as file:
    file.write(str(idx_word))
file.close()

In [142]:
print(word_idx)

{'After': 3, 'bedroom': 14, 'back': 12, 'the': 25, 'Sandra': 9, 'John': 7, 'hallway': 16, 'Following': 6, 'Afterwards': 4, 'to': 26, 'Daniel': 5, 'Then': 10, 'he': 17, 'is': 18, 'bathroom': 13, 'travelled': 27, 'she': 23, 'office': 22, '.': 1, 'garden': 15, 'Where': 11, 'went': 28, 'that': 24, 'kitchen': 20, 'moved': 21, 'journeyed': 19, '?': 2, 'Mary': 8}


In [143]:
print(idx_word)

{1: '.', 2: '?', 3: 'After', 4: 'Afterwards', 5: 'Daniel', 6: 'Following', 7: 'John', 8: 'Mary', 9: 'Sandra', 10: 'Then', 11: 'Where', 12: 'back', 13: 'bathroom', 14: 'bedroom', 15: 'garden', 16: 'hallway', 17: 'he', 18: 'is', 19: 'journeyed', 20: 'kitchen', 21: 'moved', 22: 'office', 23: 'she', 24: 'that', 25: 'the', 26: 'to', 27: 'travelled', 28: 'went'}


In [144]:
print('-')
print('inputs: integer tensor of shape (samples, max_length)')
print('inputs_train shape:', inputs_train.shape)
print('inputs_test shape:', inputs_test.shape)
print('-')
print('queries: integer tensor of shape (samples, max_length)')
print('queries_train shape:', queries_train.shape)
print('queries_test shape:', queries_test.shape)
print('-')
print('answers: binary (1 or 0) tensor of shape (samples, vocab_size)')
print('answers_train shape:', answers_train.shape)
print('answers_test shape:', answers_test.shape)
print('-')
print('Compiling...')

-
inputs: integer tensor of shape (samples, max_length)
inputs_train shape: (10000, 76)
inputs_test shape: (1000, 76)
-
queries: integer tensor of shape (samples, max_length)
queries_train shape: (10000, 4)
queries_test shape: (1000, 4)
-
answers: binary (1 or 0) tensor of shape (samples, vocab_size)
answers_train shape: (10000, 29)
answers_test shape: (1000, 29)
-
Compiling...


In [145]:
train_epochs = 120
batch_size = 32
lstm_size = 64

In [146]:
# initiating 
input_sequence = Input((story_maxlen,))
question = Input((query_maxlen,))

print('Input sequence:', input_sequence)
print('Question:', question)

# defining the encoder for the input and embedding the vocab
input_encoder_m = Sequential()
input_encoder_m.add(Embedding(input_dim=vocab_size,
                              output_dim=64))
input_encoder_m.add(Dropout(0.3))

# mapping the dimensions according to the maximum length on input
input_encoder_c = Sequential()
input_encoder_c.add(Embedding(input_dim=vocab_size,
                              output_dim=query_maxlen))
input_encoder_c.add(Dropout(0.3))

# vectorizing the questions
question_encoder = Sequential()
question_encoder.add(Embedding(input_dim=vocab_size,
                               output_dim=64,
                               input_length=query_maxlen))
question_encoder.add(Dropout(0.3))


# conctinating input stories and questions
input_encoded_m = input_encoder_m(input_sequence)
print('Input encoded m', input_encoded_m)
input_encoded_c = input_encoder_c(input_sequence)
print('Input encoded c', input_encoded_c)
question_encoded = question_encoder(question)
print('Question encoded', question_encoded)


# cross refrencing the questions against the stories
match = merge([input_encoded_m, question_encoded], mode='dot', dot_axes=(2, 2))
print(match.shape)
match = Activation('softmax')(match)
print('Match shape', match)

response = merge([match, input_encoded_c], mode='sum')
response = Permute((2, 1))(response)  
print('Response shape', response)

# mapping answers against the vector of question and stories
answer = merge([response, question_encoded], mode='concat')
print('Answer shape', answer)

answer = LSTM(64)(answer)  
answer = Dropout(0.3)(answer)
answer = Dense(vocab_size)(answer)  

# popping out prob. of answers
answer = Activation('softmax')(answer)

Input sequence: Tensor("input_9:0", shape=(?, 76), dtype=float32)
Question: Tensor("input_10:0", shape=(?, 4), dtype=float32)
Input encoded m Tensor("sequential_25/dropout_17/cond/Merge:0", shape=(?, 76, 64), dtype=float32)
Input encoded c Tensor("sequential_26/dropout_18/cond/Merge:0", shape=(?, 76, 4), dtype=float32)
Question encoded Tensor("sequential_27/dropout_19/cond/Merge:0", shape=(?, 4, 64), dtype=float32)
(?, 76, 4)
Match shape Tensor("activation_9/truediv:0", shape=(?, 76, 4), dtype=float32)
Response shape Tensor("permute_5/transpose:0", shape=(?, 4, 76), dtype=float32)
Answer shape Tensor("merge_15/concat:0", shape=(?, 4, 140), dtype=float32)


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:38: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/home/ubuntu/src/keras/keras/legacy/layers.py:464: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:43: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:48: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.


In [147]:
model = Model([input_sequence, question], answer)
model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])

In [148]:
model.fit([inputs_train, queries_train], answers_train, batch_size, train_epochs,
          validation_data=([inputs_test, queries_test], answers_test))

Train on 10000 samples, validate on 1000 samples
Epoch 1/120
10000/10000 [==============================] - 5s 470us/step - loss: 1.8832 - acc: 0.1861 - val_loss: 1.6928 - val_acc: 0.3410
Epoch 2/120
10000/10000 [==============================] - 4s 378us/step - loss: 1.4709 - acc: 0.4523 - val_loss: 1.1063 - val_acc: 0.7050
Epoch 3/120
10000/10000 [==============================] - 4s 379us/step - loss: 1.2191 - acc: 0.5927 - val_loss: 0.9681 - val_acc: 0.6740
Epoch 4/120
10000/10000 [==============================] - 4s 379us/step - loss: 1.1277 - acc: 0.6349 - val_loss: 0.8627 - val_acc: 0.7350
Epoch 5/120
10000/10000 [==============================] - 4s 380us/step - loss: 1.0168 - acc: 0.6558 - val_loss: 0.8625 - val_acc: 0.7120
Epoch 6/120
10000/10000 [==============================] - 4s 380us/step - loss: 0.9506 - acc: 0.6648 - val_loss: 0.7380 - val_acc: 0.7330
Epoch 7/120
10000/10000 [==============================] - 4s 379us/step - loss: 0.9040 - acc: 0.6732 - val_loss: 0.7

10000/10000 [==============================] - 4s 380us/step - loss: 0.0085 - acc: 0.9976 - val_loss: 0.1085 - val_acc: 0.9830
Epoch 118/120
10000/10000 [==============================] - 4s 380us/step - loss: 0.0109 - acc: 0.9975 - val_loss: 0.0969 - val_acc: 0.9850
Epoch 119/120
10000/10000 [==============================] - 4s 380us/step - loss: 0.0122 - acc: 0.9965 - val_loss: 0.1122 - val_acc: 0.9840
Epoch 120/120
10000/10000 [==============================] - 4s 381us/step - loss: 0.0120 - acc: 0.9972 - val_loss: 0.0934 - val_acc: 0.9850


In [149]:
''' Getting the feel for the test dataset
and how it is devided.
'''

' Getting the feel for the test dataset\nand how it is devided.\n'

In [150]:
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")
        

John journeyed to the hallway . After that he journeyed to the garden . Where is John ? | Prediction: garden | Ground Truth: garden
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the hallway . Where is John ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the hallway . Sandra travelled to the bedroom . Then she moved to the hallway . Where is Sandra ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the

In [151]:
print(story)

['Sandra', 'moved', 'to', 'the', 'garden', '.', 'Following', 'that', 'she', 'moved', 'to', 'the', 'kitchen', '.', 'John', 'went', 'to', 'the', 'bathroom', '.', 'Afterwards', 'he', 'travelled', 'to', 'the', 'kitchen', '.', 'Sandra', 'journeyed', 'to', 'the', 'office', '.', 'Afterwards', 'she', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'hallway', '.', 'After', 'that', 'she', 'went', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'to', 'the', 'bathroom', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.']


In [152]:
from keras.models import model_from_json
model_json = model.to_json()
with open("model_basic-conference.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model_basic-conference.h5")
print("Saved model to disk")

Saved model to disk


In [153]:
json_file = open('model_basic-conference.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights("model_basic-conference.h5")

/home/ubuntu/src/keras/keras/engine/topology.py:1269: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  return cls(**config)


In [154]:
test_stories[0]

(['John',
  'journeyed',
  'to',
  'the',
  'hallway',
  '.',
  'After',
  'that',
  'he',
  'journeyed',
  'to',
  'the',
  'garden',
  '.'],
 ['Where', 'is', 'John', '?'],
 'garden')

In [155]:
loaded_model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = loaded_model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")


John journeyed to the hallway . After that he journeyed to the garden . Where is John ? | Prediction: garden | Ground Truth: garden
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the hallway . Where is John ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the hallway . Sandra travelled to the bedroom . Then she moved to the hallway . Where is Sandra ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John journeyed to the hallway . After that he journeyed to the garden . John moved to the office . Following that he went to the

In [156]:
print(current_story)

[[ 0  0  0  5 27 26 25 22  1  3 24 17 28 12 26 25 20  1  5 19 26 25 22  1
   3 24 17 28 26 25 20  1  8 19 26 25 13  1  6 24 23 27 26 25 16  1  5 28
  12 26 25 16  1  4 17 28 12 26 25 15  1  8 27 26 25 13  1  6 24 23 28 12
  26 25 20  1]]


In [157]:
print(current_query)

[[11 18  8  2]]


In [158]:
print(len(current_query))

1


In [159]:
print(test_stories[0])

(['John', 'journeyed', 'to', 'the', 'hallway', '.', 'After', 'that', 'he', 'journeyed', 'to', 'the', 'garden', '.'], ['Where', 'is', 'John', '?'], 'garden')
